  # Evolution de la part de la production d'éléctricité renouvable dans la consommation globale électrique française de 2013 à 2021¶

## importation des différents modules

In [ ]:
import re
import unidecode
import json

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
from matplotlib.backends.backend_pdf import PdfPages

_Configuration de l'affichage des données:_ aucun chiffre après la virgule

In [ ]:
##precision floats
pd.options.display.float_format = '{:,.0f}'.format

# Origine des données

**Consommation électrique**  
Les données de l'évolution de la consommation d'éléctricité au cours du temps sont disponibles sur : [**data_gouv_conso**](https://www.data.gouv.fr/fr/datasets/consommation-quotidienne-brute-2012-a-2021/#_).  
Nous les récupérons sous forme d'un fichier en format CSV dont chaque ligne correspond à la consommation électrique quotidienne par demi-heure en MW. L'URL est: https://opendata.reseaux-energies.fr/explore/dataset/consommation-quotidienne-brute/download?format=csv&timezone=Europe/Berlin&use_labels_for_header=false

**Production électrique**  
En parallèle, les données de l'évolution de la production d'électricité hydraulique, solaire, éolienne et bio-énergie au cours du temps sont disponibles sur : [**data_gouv_prod**](https://www.data.gouv.fr/fr/datasets/production-quotidienne-delectricite-par-filiere-depuis-janvier-2013/#_).  
Nous les récupérons sous forme d'un fichier en format CSV dont chaque ligne correspond à la production électrique quotidienne par demi-heure en MW. L'URL est: https://opendata.reseaux-energies.fr/explore/dataset/production-quotidienne-filiere/download?format=csv&timezone=Europe/Berlin&use_labels_for_header=false

## Téléchargemet et configuration des données
**NB**: on séléctionne uniquement les colonnes qui nous intéressent pour la suite de l'étude

### Consommation électrique

In [ ]:
#upload electric consumption:
conso_elec= pd.read_csv("https://opendata.reseaux-energies.fr/explore/dataset/consommation-quotidienne-brute/download?format=csv&timezone=Europe/Berlin&use_labels_for_header=false", sep=';',
                       usecols=[1,2,8])

In [ ]:
# config & convert date to datetime
elec_conso = conso_elec.rename(columns={'consommation_brute_electricite_rte':'conso_elec'}).dropna().copy()

elec_conso['date'] = pd.to_datetime(elec_conso['date'])#, format='%d/%m%/%Y')

elec_conso = elec_conso.sort_values('date')
print(elec_conso.dtypes)
elec_conso.tail()

On agglomère les données en un tableau de consommation quotidienne en GW

In [ ]:
#daily consumption & convert to GW
elec_conso_ = elec_conso.groupby('date')['conso_elec'].sum().reset_index()

elec_conso_['conso_elec'] = elec_conso_['conso_elec'].map(lambda x: x/10**3)

elec_conso_

**NB:** On peut s'étonner de retrouver des consommations électriques futuristes

### Production électrique

In [ ]:
#upload electric production:
prod_elec= pd.read_csv("https://opendata.reseaux-energies.fr/explore/dataset/production-quotidienne-filiere/download?format=csv&timezone=Europe/Berlin&use_labels_for_header=false",
                       sep=';', usecols=[1,2,3,8,10,11,12])


In [ ]:
# config & convert date to datetime
cols_prod = ['date', 'heure', 'prod_totale', 'hydrau', 'solaire', 'eolien', 'bio']

elec_prod = prod_elec.copy()
elec_prod.columns = cols_prod

elec_prod['date'] = pd.to_datetime(elec_prod['date'])#, format='%d/%m%/%Y')

elec_prod = elec_prod.sort_values('date')
print(elec_prod.dtypes)
elec_prod.tail()

In [ ]:
On agglomère les données en un tableau de production quotidienne en GW

In [ ]:
#daily prod & convert to GW:
elec_prod_ = elec_prod.groupby('date')[['prod_totale', 'hydrau', 'solaire', 'eolien', 'bio']].sum().reset_index()

elec_prod_[['prod_totale', 'hydrau', 'solaire', 'eolien', 'bio']] = elec_prod_[['prod_totale', 'hydrau', 'solaire', 'eolien', 'bio']].apply(lambda x: x/10**3)

elec_prod_

### Fusion des 2 fichiers

In [ ]:
elec_df = pd.merge(elec_prod_, elec_conso_, on='date', how='left')

elec_df

Vérifions qu'il n'y a pas de données manquantes

In [ ]:
print(pd.isnull(elec_df).sum())

elec_df[pd.isna(elec_df['conso_elec'])]

Des données de consommation sont manquantes pour les mois de janvier et février 2021. On restreind notre plage d'étude aux années 2013 à 2020.

In [ ]:
elec_df = elec_df.set_index('date').loc['2012-01-01':'2020-12-31']

elec_df

In [ ]:
On crée les colonnes "année", "mois", "jour_semaine" pour chaque date

In [ ]:
elec_df['annee'] = elec_df.index.year
elec_df['mois'] = elec_df.index.month
elec_df['jour_sem'] = elec_df.index.day_name()

elec_df

### conversion au format csv

In [ ]:
elec_df.to_csv('electricite_conso_prod_renouvelable_france_2013_2020_042021.csv')

# Analyses

## Statisiques

Quelques statistiques au travers de la fonction describe

In [ ]:
elec_df[['conso_elec', 'prod_totale', 'hydrau', 'solaire', 'eolien', 'bio',]].describe()

**Remarques:** 
    - la production d'électricité à partir d'énergies renouvelables se caractérise par une forte variabilité annuelle. On observe une forte variabilité (min vs max) de ces productions sur la période considérée. Pour confirmation, on observera l'évolution intra-annuelle.
    - L'évolution du potentiel de production éolien semble avoir ete plus imortant que celui du solaire (différence min-max).

## Saisonnalité

In [ ]:
fig, axes = plt.subplots(5, 1, figsize=(11, 15), sharex=True)
for name, ax in zip(['conso_elec', 'hydrau', 'solaire', 'eolien', 'bio'], axes):
    sns.boxplot(data=elec_df, x='mois', y=name, ax=ax)
    ax.set_ylabel('GWh')
    ax.set_title(name)
# Remove the automatic x-axis label from all but the bottom subplot
#if ax != axes[-1]:
#    ax.set_xlabel('')

**Commentaires:** 
    - confirmation de la saisonnalité de la consommation électrique, avec des pics durant les mois les plus froids (novembre à mars),  
    - 

## Saisonnalité hebdomadaire

In [ ]:
fig, ax = plt.subplots(figsize=(14,5))
ax = sns.boxplot(data=elec_df, x='jour_sem', y='conso_elec')
ax.set_title(f'Evolution hebdomadaire de la consommation électrique (GWh)\n',
             fontweight='bold', fontsize=16, color='C0')
ax.set_ylabel('consommation_quotidienne (GWh)')
ax.set_xlabel('jour_semaine')
plt.yticks(fontsize=12), plt.xticks(fontsize=12)
;

**Remarques:** 
    - la consommation d'électricité est plus faible lors du week-end, mais avec un écart qu'on aurait supposé pls important avec les autres jours de la semaine.
    cru plus imortantdans une proportion à partir d'énergies renouvelables se caractérise par une forte variabilité annuelle. On observe une forte variabilité (min vs max) de ces productions sur la période considérée. Pour confirmation, on observera l'évolution intra-annuelle.
    - L'évolution du potentiel de production éolien semble avoir ete plus imortant que celui du solaire (différence min-max).

L'analyse de saisonnalité peut également être conduite par l'[autocorrelation_plot](https://pandas.pydata.org/pandas-docs/stable/user_guide/visualization.html) comme nous le verrons dans quelques instants

## Evolution au cours dela période considérée

**NB_1:** afin d'obtenir une visualisation plus apropriée des évolutions annuelles, nous allons modifier la fréquence des données (**resample**) en passant d'une fréquence quotidienne à une fréquence mensuelle (**downsampling**)  
**NB_2:** la donnée mensuelle sera notifiée "nan" si pour la colonne considérée, le mois comporte moins de 28 données (*min-count=28*)

In [ ]:
cols_month = ['prod_totale', 'conso_elec', 'hydrau', 'solaire', 'eolien', 'bio']
elec_month = elec_df[cols_month].resample('M').sum(min_count=28)

elec_month.head()

**Graphique de l'évolution de la consommation éléctrisue versus la production d'électrcité renouvable**

In [ ]:
import matplotlib.dates as mdates

fig, ax = plt.subplots(figsize=(14,7))
ax.plot(elec_month['conso_elec'], color='black', label='Consommation')
elec_month[['hydrau', 'solaire', 'eolien', 'bio']].plot.area(ax=ax, linewidth=0)
ax.set_title(f"Evolution annuelle de la consommation électrique\n et de la production d'électricité renouvable(GWh)\n",
             fontweight='bold', fontsize=16, color='C0')
ax.xaxis.set_major_locator(mdates.YearLocator())
ax.set_xlabel('année', fontsize=14)
ax.legend()
ax.set_ylabel('Total mensuel (GWh)');

**Remarques:**  
On peut observer :  
    * la saisonnalité des différents items (en dehors de la bio-énergie),  
    * la relative constance de la consommation électrique au cours des années, voire sa légère tendance à la baisse (à confirmer),  
    * la part croissante de l'éolien, et dans une moindre mesure du solaire, dans la contribution à la production d'éléctricité.

**Observation de l'évolution de la part des énergies renouvelables dans la consommation éléctrique**

"Resamplons" par année

In [ ]:
elec_year = elec_df[cols_month].resample('A').sum()

#set index on year:
elec_year = elec_year.set_index(elec_year.index.year)

elec_year

Calcul du ratio "renouvelables/consommation"

In [ ]:
elec_year['renouvelables'] = [w+x+y+z for w,x,y,z in zip(elec_year['hydrau'], elec_year['solaire'], elec_year['eolien'],
                                                         elec_year['bio'])]

elec_year['renouvelables/consommation'] = [(x/c)*100 for x,c in zip(elec_year['renouvelables'], elec_year['conso_elec'])]

elec_year

*Tracé du graphique*

In [ ]:
import matplotlib.ticker as mtick

fig, ax = plt.subplots(figsize=(14,7))
ax = elec_year['renouvelables/consommation'].plot.bar(color='C0')
ax.set_ylabel('ratio', fontsize=14), ax.set_ylabel('année', fontsize=14)
ax.set_ylim(0, 30)
ax.set_title(f"Part des énergies renouvelables dans la consommation d'électricité\n France - 2013 à 2020\n",
             fontweight='bold', fontsize=16, color='C0')
plt.gca().yaxis.set_major_formatter(mtick.PercentFormatter())
plt.grid(axis='y', c='gainsboro')
plt.xticks(fontsize=14, rotation=0), plt.yticks(fontsize=14);

**Remarques:**  
    * la part de la production électrique "renouvelable" dans la consommation globale d'électrcité est passée de 20% en 2013 à 28% en 2020  
    * personnellement assez surpris par la part de la production électrique renouvelable dans la consommation électrique globale. légère surestimation ? La production hydroélectrique y est pour beaucoup

## Tendances

**NB_1** utilisons la moyenne mobile (**methode *rolling()***) pour visualiser les tendances d'évolution de chaque production "renouvelbale" au cours des années  
**NB_2:** examinons les moyennes mobiles sur la saisonnalité annuelle

Création de la colonne "renouvlables", cumul des productions hydro+éolien+solaire+bio

In [ ]:
elec_df['renouvelables'] = [w+x+y+z for w,x,y,z in zip(elec_df['hydrau'], elec_df['solaire'], elec_df['eolien'],
                                                       elec_df['bio'])]

cols_month.append('renouvelables')

In [ ]:
elec_yearmob = elec_df[cols_month].rolling(window=365, center=True).mean()

Tracé du graphique de tendance

In [ ]:
fig, ax = plt.subplots(figsize=(14,7))
for x in ['hydrau', 'solaire', 'eolien', 'bio', 'renouvelables']:
    ax.plot(elec_yearmob[x], label=x)
    #ax.xaxis.set_major_formatter(mdates.DateFormatter('%Y-%m-%d'))
    ax.xaxis.set_major_locator(mdates.YearLocator())
    ax.legend()
    ax.set_ylabel('Production (GWh)')
    ax.set_title(f"Tendance de la production électrique renouvelable (moyenne mobile annuelle)")
    plt.grid(axis='y', c='gainsboro');

**Conclusion:**  
    * la production d'électricité "renouvelable" augmente au cours des années, conformément aux annonces politiques  
    * le principal contributeur de cette hausee est l'énergie éolienne et dans une moindre mesure la production éolienne et les bioénergies  
    * la production hydroélectrique a tendance à régresser au cours des années (lien avec la fréquence des sécheresses sur la même période ?) mais participe toujours à hauteur de 50% dans la production d'électricité renouvelable.